In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker #For changing ticker location and formatting
import seaborn as sns

from sklearn.linear_model import LinearRegression, Ridge, RidgeCV, Lasso, LassoCV
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn import metrics
from sklearn.metrics import r2_score, mean_squared_error
from sklearn.preprocessing import StandardScaler, PolynomialFeatures

In [2]:
#Load in clean CSV
test = pd.read_csv('./datasets/clean_recoded_test_ames.csv', index_col = 'id')
test.head()
    #I'm at the end of the worflow, but I just realized I always should have been reading in the data files by making the 'id' the index column.

pid  ms_subclass ms_zoning  lot_frontage  lot_area street alley  \
id                                                                            
2658  902301120          190        RM          69.0      9142   Pave  Grvl   
2718  905108090           90        RL           0.0      9662   Pave   NaN   
2414  528218130           60        RL          58.0     17104   Pave   NaN   
1989  902207150           30        RM          60.0      8520   Pave   NaN   
625   535105100           20        RL           0.0      9500   Pave   NaN   

      lot_shape land_contour utilities  ... misc_val  mo_sold yr_sold  \
id                                      ...                             
2658          4          Lvl    AllPub  ...        0        4    2006   
2718          3          Lvl    AllPub  ...        0        8    2006   
2414          3          Lvl    AllPub  ...        0        9    2006   
1989          4          Lvl    AllPub  ...        0        7    2007   
625           3          Lvl    AllPub  ...        0        7    2009   

     sale_type age_at_sale age_since_remod bsmnt_fin_sf  sold_in_crisis  \
id                                                                        
2658       WD           96              56            0               0   
2718       WD           29              29            0               0   
2414       New           0               0          554               0   
1989       WD           84               1            0               0   
625        WD           46              46          609               1   

      has_wood_deck  has_pool  
id                             
2658              0         0  
2718              1         0  
2414              1         0  
1989              0         0  
625               0         0  

[5 rows x 85 columns]

In [3]:
#Categorical columns I want to use
fewer_cats = test[['ms_zoning', 'neighborhood', 'bldg_type', 'house_style', 'foundation', 'garage_type', 'mo_sold']]
fewer_cats

ms_zoning neighborhood bldg_type house_style foundation garage_type  \
id                                                                         
2658        RM      OldTown    2fmCon      2Story      Stone      Detchd   
2718        RL       Sawyer    Duplex      1Story     CBlock      Attchd   
2414        RL      Gilbert      1Fam      2Story      PConc      Attchd   
1989        RM      OldTown      1Fam      1Story     CBlock      Detchd   
625         RL        NAmes      1Fam      1Story     CBlock      Attchd   
...        ...          ...       ...         ...        ...         ...   
1662        RL       NWAmes      1Fam      2Story     CBlock      Attchd   
1234        RL        NAmes      1Fam      2Story     CBlock      Attchd   
1373        RL       Sawyer      1Fam      1Story     CBlock      Attchd   
1672        RL        NAmes      1Fam      1Story      PConc      Detchd   
1939        RL        NAmes      1Fam      1Story     CBlock      Attchd   

      mo_sold  
id             
2658        4  
2718        8  
2414        9  
1989        7  
625         7  
...       ...  
1662       11  
1234        8  
1373        8  
1672        5  
1939        3  

[878 rows x 7 columns]

In [4]:
numeric_test = test.select_dtypes(exclude = 'object')
numeric_test.head(5)

pid  ms_subclass  lot_frontage  lot_area  lot_shape  land_slope  \
id                                                                            
2658  902301120          190          69.0      9142          4           3   
2718  905108090           90           0.0      9662          3           3   
2414  528218130           60          58.0     17104          3           3   
1989  902207150           30          60.0      8520          4           3   
625   535105100           20           0.0      9500          3           3   

      overall_qual  overall_cond  year_built  year_remod/add  ...  fence  \
id                                                            ...          
2658             6             8        1910            1950  ...      0   
2718             5             4        1977            1977  ...      0   
2414             7             5        2006            2006  ...      0   
1989             5             6        1923            2006  ...      0   
625              6             5        1963            1963  ...      0   

      misc_val  mo_sold  yr_sold  age_at_sale  age_since_remod  bsmnt_fin_sf  \
id                                                                             
2658         0        4     2006           96               56             0   
2718         0        8     2006           29               29             0   
2414         0        9     2006            0                0           554   
1989         0        7     2007           84                1             0   
625          0        7     2009           46               46           609   

      sold_in_crisis  has_wood_deck  has_pool  
id                                             
2658               0              0         0  
2718               0              1         0  
2414               0              1         0  
1989               0              0         0  
625                1              0         0  

[5 rows x 63 columns]

In [5]:
cols_to_drop = ['pid', 'garage_yr_blt', 'sold_in_crisis', 'mo_sold']
numeric_test = numeric_test.drop(cols_to_drop, axis = 1)

In [10]:
#The remaining numeric columns I want to use
numeric_test.head()

ms_subclass  lot_frontage  lot_area  lot_shape  land_slope  \
id                                                                 
2658          190          69.0      9142          4           3   
2718           90           0.0      9662          3           3   
2414           60          58.0     17104          3           3   
1989           30          60.0      8520          4           3   
625            20           0.0      9500          3           3   

      overall_qual  overall_cond  year_built  year_remod/add  mas_vnr_area  \
id                                                                           
2658             6             8        1910            1950           0.0   
2718             5             4        1977            1977           0.0   
2414             7             5        2006            2006           0.0   
1989             5             6        1923            2006           0.0   
625              6             5        1963            1963         247.0   

      ...  screen_porch  pool_area  fence  misc_val  yr_sold  age_at_sale  \
id    ...                                                                   
2658  ...             0          0      0         0     2006           96   
2718  ...             0          0      0         0     2006           29   
2414  ...             0          0      0         0     2006            0   
1989  ...             0          0      0         0     2007           84   
625   ...           185          0      0         0     2009           46   

      age_since_remod  bsmnt_fin_sf  has_wood_deck  has_pool  
id                                                            
2658               56             0              0         0  
2718               29             0              1         0  
2414                0           554              1         0  
1989                1             0              0         0  
625                46           609              0         0  

[5 rows x 59 columns]

In [11]:
numeric_test.columns

Index(['ms_subclass', 'lot_frontage', 'lot_area', 'lot_shape', 'land_slope',
       'overall_qual', 'overall_cond', 'year_built', 'year_remod/add',
       'mas_vnr_area', 'exter_qual', 'exter_cond', 'bsmt_qual', 'bsmt_cond',
       'bsmt_exposure', 'bsmtfin_type_1', 'bsmtfin_sf_1', 'bsmtfin_type_2',
       'bsmtfin_sf_2', 'bsmt_unf_sf', 'total_bsmt_sf', 'heating_qc',
       'central_air', 'electrical', '1st_flr_sf', '2nd_flr_sf',
       'low_qual_fin_sf', 'gr_liv_area', 'bsmt_full_bath', 'bsmt_half_bath',
       'full_bath', 'half_bath', 'bedroom_abvgr', 'kitchen_abvgr',
       'kitchen_qual', 'totrms_abvgrd', 'functional', 'fireplaces',
       'fireplace_qu', 'garage_finish', 'garage_cars', 'garage_area',
       'garage_qual', 'garage_cond', 'paved_drive', 'wood_deck_sf',
       'open_porch_sf', 'enclosed_porch', '3ssn_porch', 'screen_porch',
       'pool_area', 'fence', 'misc_val', 'yr_sold', 'age_at_sale',
       'age_since_remod', 'bsmnt_fin_sf', 'has_wood_deck', 'has_pool'],
     

In [9]:
numeric_test.info()

<class 'pandas.core.frame.DataFrame'>
Index: 878 entries, 2658 to 1939
Data columns (total 59 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   ms_subclass      878 non-null    int64  
 1   lot_frontage     878 non-null    float64
 2   lot_area         878 non-null    int64  
 3   lot_shape        878 non-null    int64  
 4   land_slope       878 non-null    int64  
 5   overall_qual     878 non-null    int64  
 6   overall_cond     878 non-null    int64  
 7   year_built       878 non-null    int64  
 8   year_remod/add   878 non-null    int64  
 9   mas_vnr_area     878 non-null    float64
 10  exter_qual       878 non-null    int64  
 11  exter_cond       878 non-null    int64  
 12  bsmt_qual        878 non-null    int64  
 13  bsmt_cond        878 non-null    int64  
 14  bsmt_exposure    878 non-null    int64  
 15  bsmtfin_type_1   878 non-null    int64  
 16  bsmtfin_sf_1     878 non-null    int64  
 17  bsmtfin_type_2   

In [16]:
comb_test_data = numeric_test.join(fewer_cats, how = 'inner')
comb_test_data.head()

ms_subclass  lot_frontage  lot_area  lot_shape  land_slope  \
id                                                                 
2658          190          69.0      9142          4           3   
2718           90           0.0      9662          3           3   
2414           60          58.0     17104          3           3   
1989           30          60.0      8520          4           3   
625            20           0.0      9500          3           3   

      overall_qual  overall_cond  year_built  year_remod/add  mas_vnr_area  \
id                                                                           
2658             6             8        1910            1950           0.0   
2718             5             4        1977            1977           0.0   
2414             7             5        2006            2006           0.0   
1989             5             6        1923            2006           0.0   
625              6             5        1963            1963         247.0   

      ...  bsmnt_fin_sf  has_wood_deck  has_pool  ms_zoning  neighborhood  \
id    ...                                                                   
2658  ...             0              0         0         RM       OldTown   
2718  ...             0              1         0         RL        Sawyer   
2414  ...           554              1         0         RL       Gilbert   
1989  ...             0              0         0         RM       OldTown   
625   ...           609              0         0         RL         NAmes   

      bldg_type  house_style  foundation  garage_type  mo_sold  
id                                                              
2658     2fmCon       2Story       Stone       Detchd        4  
2718     Duplex       1Story      CBlock       Attchd        8  
2414       1Fam       2Story       PConc       Attchd        9  
1989       1Fam       1Story      CBlock       Detchd        7  
625        1Fam       1Story      CBlock       Attchd        7  

[5 rows x 66 columns]

In [17]:
comb_test_data.columns

Index(['ms_subclass', 'lot_frontage', 'lot_area', 'lot_shape', 'land_slope',
       'overall_qual', 'overall_cond', 'year_built', 'year_remod/add',
       'mas_vnr_area', 'exter_qual', 'exter_cond', 'bsmt_qual', 'bsmt_cond',
       'bsmt_exposure', 'bsmtfin_type_1', 'bsmtfin_sf_1', 'bsmtfin_type_2',
       'bsmtfin_sf_2', 'bsmt_unf_sf', 'total_bsmt_sf', 'heating_qc',
       'central_air', 'electrical', '1st_flr_sf', '2nd_flr_sf',
       'low_qual_fin_sf', 'gr_liv_area', 'bsmt_full_bath', 'bsmt_half_bath',
       'full_bath', 'half_bath', 'bedroom_abvgr', 'kitchen_abvgr',
       'kitchen_qual', 'totrms_abvgrd', 'functional', 'fireplaces',
       'fireplace_qu', 'garage_finish', 'garage_cars', 'garage_area',
       'garage_qual', 'garage_cond', 'paved_drive', 'wood_deck_sf',
       'open_porch_sf', 'enclosed_porch', '3ssn_porch', 'screen_porch',
       'pool_area', 'fence', 'misc_val', 'yr_sold', 'age_at_sale',
       'age_since_remod', 'bsmnt_fin_sf', 'has_wood_deck', 'has_pool',
      

In [20]:
comb_test_data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 878 entries, 2658 to 1939
Data columns (total 66 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   ms_subclass      878 non-null    int64  
 1   lot_frontage     878 non-null    float64
 2   lot_area         878 non-null    int64  
 3   lot_shape        878 non-null    int64  
 4   land_slope       878 non-null    int64  
 5   overall_qual     878 non-null    int64  
 6   overall_cond     878 non-null    int64  
 7   year_built       878 non-null    int64  
 8   year_remod/add   878 non-null    int64  
 9   mas_vnr_area     878 non-null    float64
 10  exter_qual       878 non-null    int64  
 11  exter_cond       878 non-null    int64  
 12  bsmt_qual        878 non-null    int64  
 13  bsmt_cond        878 non-null    int64  
 14  bsmt_exposure    878 non-null    int64  
 15  bsmtfin_type_1   878 non-null    int64  
 16  bsmtfin_sf_1     878 non-null    int64  
 17  bsmtfin_type_2   

In [41]:
comb_test_data['neighborhood'].value_counts()
    #Some neighborhoods that appear in training data like Landmark, GreenHill, Blueste don't appear in test data.

neighborhood
NAmes      133
CollgCr     87
OldTown     76
Somerst     52
Edwards     50
Gilbert     49
NridgHt     44
NWAmes      44
Sawyer      40
SawyerW     38
Mitchel     32
Crawfor     32
BrkSide     32
Timber      24
IDOTRR      24
NoRidge     23
ClearCr     17
SWISU       16
MeadowV     13
StoneBr     13
BrDale      11
Veenker      7
Blmngtn      6
NPkVill      6
Greens       5
Blueste      4
Name: count, dtype: int64

In [40]:
test_dum = pd.get_dummies(comb_test_data, dtype = int, sparse = False, drop_first = True)
test_dum

ms_subclass  lot_frontage  lot_area  lot_shape  land_slope  \
id                                                                 
2658          190          69.0      9142          4           3   
2718           90           0.0      9662          3           3   
2414           60          58.0     17104          3           3   
1989           30          60.0      8520          4           3   
625            20           0.0      9500          3           3   
333           160          21.0      1890          4           3   
1327           20          52.0      8516          4           3   
858            20           0.0      9286          3           2   
95            160          39.0      3515          4           3   
1568           20          75.0     10125          4           3   
2482          120          50.0      7175          4           3   
1364           30          60.0      7200          4           3   
2584           20          75.0     11310          4           3   
818            90           0.0      7976          4           3   
2673           70          69.0     11737          3           3   
2089           20          60.0      9060          4           3   
1297          190          60.0     10800          4           3   
790            20          68.0      9571          4           3   
2616           20          80.0     10800          4           3   
720            70         121.0     17671          4           3   
222            20           0.0      8246          3           3   
557            20           0.0      8499          3           3   
1148          120          50.0      8012          4           3   
2766           80           0.0     21453          3           1   
534            20          80.0      9605          4           3   
1452           20          60.0      7180          3           3   
630            50           0.0     12513          3           3   
2648           70          50.0      9000          4           3   
125            85          80.0      8800          4           3   
1904           50          51.0      3500          4           3   
1670           20           0.0      7340          3           3   
756            30          52.0      6240          4           3   
717            70          65.0     11700          3           3   
1032           20          80.0     10000          4           3   
852            20          75.0     11166          4           3   
1731           60          58.0     13204          3           3   
2639           50          60.0      5520          4           3   
2071           20           0.0      9000          4           3   
1267           20          74.0      8892          4           3   
1851           20          73.0      7321          3           3   
567           160          40.0      3951          4           3   
2439           60           0.0     11214          3           3   
1898           20          75.0      7388          4           3   
647            20          75.0     14559          4           3   
2256          120          46.0      4054          3           3   
979           160          21.0      1533          4           3   
1444           60          68.0     11250          3           3   
2485           20          60.0      7800          4           3   
157            20          74.0      5868          4           3   
88             20          75.0      7500          4           3   
2003           50          52.0      9439          4           3   
186            70          50.0      9000          4           3   
1425           20          65.0      9345          3           3   
2695           50          60.0      7200          4           3   
738            50          60.0      6000          4           3   
395            20          61.0      7930          4           3   
1353           50          60.0      9120          4          

In [ ]:
#### This has 121 columns - final test data had 125 columns. Need to fix to run model.

In [37]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

In [38]:
test_dum.head()

ms_subclass  lot_frontage  lot_area  lot_shape  land_slope  \
id                                                                 
2658          190          69.0      9142          4           3   
2718           90           0.0      9662          3           3   
2414           60          58.0     17104          3           3   
1989           30          60.0      8520          4           3   
625            20           0.0      9500          3           3   

      overall_qual  overall_cond  year_built  year_remod/add  mas_vnr_area  \
id                                                                           
2658             6             8        1910            1950           0.0   
2718             5             4        1977            1977           0.0   
2414             7             5        2006            2006           0.0   
1989             5             6        1923            2006           0.0   
625              6             5        1963            1963         247.0   

      exter_qual  exter_cond  bsmt_qual  bsmt_cond  bsmt_exposure  \
id                                                                  
2658           3           2          2          3              1   
2718           3           3          4          3              1   
2414           4           3          4          4              3   
1989           4           3          3          3              1   
625            3           3          4          3              1   

      bsmtfin_type_1  bsmtfin_sf_1  bsmtfin_type_2  bsmtfin_sf_2  bsmt_unf_sf  \
id                                                                              
2658               1             0               1             0         1020   
2718               1             0               1             0         1967   
2414               6           554               1             0          100   
1989               1             0               1             0          968   
625                4           609               1             0          785   

      total_bsmt_sf  heating_qc  central_air  electrical  1st_flr_sf  \
id                                                                     
2658           1020           4            0         2.0         908   
2718           1967           3            1         5.0        1967   
2414            654           5            1         5.0         664   
1989            968           3            1         5.0         968   
625            1394           4            1         5.0        1394   

      2nd_flr_sf  low_qual_fin_sf  gr_liv_area  bsmt_full_bath  \
id                                                               
2658        1020                0         1928               0   
2718           0                0         1967               0   
2414         832                0         1496               1   
1989           0                0          968               0   
625            0                0         1394               1   

      bsmt_half_bath  full_bath  half_bath  bedroom_abvgr  kitchen_abvgr  \
id                                                                         
2658               0          2          0              4              2   
2718               0          2          0              6              2   
2414               0          2          1              3              1   
1989               0          1          0              2              1   
625                0          1          1              3              1   

      kitchen_qual  totrms_abvgrd  functional  fireplaces  fireplace_qu  \
id                                                                        
2658             2              9           8           0             0   
2718             3             10           8           0             0   
2414             4              7           8           1             4   
1989             3              5           8         